In [20]:
from random import randint
import pandas as pd

In [46]:
#Methods
def distance_func (urinals):
    distance_sum = 0;
    occupied = 0;
    
    #Convert to int
    urinals = list(map(int, urinals))
    
    for i in range (0,len(urinals)):
        
        if urinals[i] != 0:
            occupied+= 1
            occupiedLeft = False
            occupiedRight = False
            
            #Find nearest occupied urinal to the right
            for j in range (i+1, len(urinals)):
                
                if urinals [j] != 0:
                    right = j - i - 1
                    occupiedRight = True
                    break;

            #Find nearest occupied urinal to the left 
            for k in range (i-1, -1, -1):
                
                if urinals[k] != 0:
                    left = i - k + 1
                    occupiedLeft = True
                    break;
            
            # Find distance to closeset urinal
            if (occupiedRight == True & occupiedLeft == True):
                distance_sum += (right if (right < left) else left)     
            elif (occupiedRight == False & occupiedLeft == False):
                distance_sum += 0
            else:
                distance_sum += (right if (occupiedLeft == False) else left)
            
    if occupied == 0:
        return 0
    
    return distance_sum / occupied

def random_model (urinals):
    empty = []
    unoccupied = 0
    
    # Find number to insert
    copy = list(map(int, urinals))
    num = max(copy) + 1

    #Find empty urinals
    for i in range (0 , len(urinals)):
        
        if urinals[i] == 0:
            empty.append(i)
            unoccupied += 1
    
    if not empty:
        return [0, 0, 0, 0]
    
    #'Occupy' a random urinal
    urinals[empty[randint (0, len(empty) -1)]] = num #str(num) 
    return urinals

def max_dist_model (urinals):
    empty = []
    unoccupied = 0
    max_dist = 0
    index = None
    
    #Find number to insert 
    copy = list(map(int, urinals))
    num = max(copy) + 1
    
    #Find empty urinals
    for i in range (0 , len(urinals)):
        
        if urinals[i] == 0:
            empty.append(i)
            unoccupied += 1

    #Return if no unoccupied urinals
    if not empty:
        return urinals
    
    # "Insert" into each unoccupied urinal and compare distance values of simulation
    for j in range (0, len(empty)): 
        
        copy = list(urinals)
        copy[empty[j]] = len(urinals) - unoccupied + 1
        dist = distance_func (copy)
        if (dist > max_dist):
            max_dist = dist
            index = j
        
        # If two urinals have the same max distance for that config, randomly choose one
        elif (dist == max_dist):
            coinflip = randint(0,2)
            if (coinflip == 1):
                index = j
                
    if index is None:
        return urinals
    
    urinals[empty[index]] = num #str(num)
    return urinals

def compare_models (urinals):
    copy = list(urinals)
    random_config_pred = 0
    random_dist_pred = 0
    max_config_pred = 0
    max_dist_pred = 0
    
    dist = distance_func(urinals)
    print ("Config: ", urinals)
    print ("Dist: ", distance_func(urinals))
    
    #Simulate condition before last occupation
    copy[copy.index(max(copy))] = 0
    
    #Random Model Simulation
    random = list(copy)
    random = random_model(random)
    random_dist = distance_func(random)
    print ("Random: ", random)
    print ("Random Dist: ", random_dist)
    
    #Max Distance Model Simulation
    maxd = list(copy)
    maxd = max_dist_model(maxd)
    max_dist = distance_func (maxd)
    print ("Max: ", maxd)
    print ("Max Dist: ", max_dist)
    
    if random == urinals:
        random_config_pred = 1
    if random_dist_pred == dist:
        random_dist_pred = 1
    if maxd == urinals:
        max_config_pred = 1
    if max_dist == dist:
        max_dist_pred = 1
    
    return random_config_pred, random_dist_pred, max_config_pred, max_dist_pred

def eval (df):
    random_config_pred = 0
    random_dist_pred = 0
    max_config_pred = 0
    max_dist_pred = 0
    data = df.values.tolist()

    for config in data:
        a,b,c,d = compare_models(config)
        random_config_pred += a
        random_dist_pred += b
        max_config_pred += c
        max_dist_pred += d
        
    size = len(df.index)
    print ("PREDICTION ACCURACY")
    print ("Random :", random_config_pred/size, " ", random_dist_pred/size)
    print ("Max :" , max_config_pred/size, max_dist_pred/size)
    
    return random_config_pred/size, random_dist_pred/size, max_config_pred/size, max_dist_pred/size

In [47]:
#Prepare the dataset
data = pd.read_csv("urinal_dataset.csv")
data.columns = ['Urinal 1', 'Urinal 2', 'Urinal 3', 'Urinal 4', 'Urinal 5', 'Urinal 6']
print(data)

    Urinal 1  Urinal 2  Urinal 3  Urinal 4  Urinal 5  Urinal 6
0          0         0         0         1         0         0
1          0         0         0         0         0         1
2          0         0         0         0         1         0
3          0         0         1         0         0         0
4          0         2         0         0         1         0
5          0         2         0         1         0         0
6          0         2         0         0         0         1
7          0         1         0         0         0         2
8          1         0         0         0         2         0
9          0         0         0         2         0         1
10         0         2         0         0         1         0
11         3         0         2         0         1         0
12         1         0         0         2         0         3
13         0         1         0         2         0         3
14         3         0         2         0         1   

In [49]:
random_config_pred = 0
random_dist_pred = 0
max_config_pred = 0
max_dist_pred = 0
trials = 1000

#Run simulation
for x in range (0, trials):
    a, b, c, d = eval(data)
    
    random_config_pred += a
    random_dist_pred += b
    max_config_pred += c
    max_dist_pred += d

print("-------------------------------------------------------------------------")
print("Final results after ", trials, " simulations: \n")
print("Random model's configuration prediction: ", random_config_pred/trials)
print("Random model's distance prediction: ", random_dist_pred/trials) 
print ("Max_distance model's configuration prediction: ", max_config_pred/trials)
print ("Max_distance model's distance prediction: ", max_dist_pred/trials)

Config:  [0, 0, 0, 1, 0, 0]
Dist:  0.0
Random:  [0, 0, 0, 0, 1, 0]
Random Dist:  0.0
Max:  [0, 0, 0, 1, 0, 0]
Max Dist:  0.0
Config:  [0, 0, 0, 0, 0, 1]
Dist:  0.0
Random:  [0, 0, 0, 0, 0, 1]
Random Dist:  0.0
Max:  [0, 0, 0, 1, 0, 0]
Max Dist:  0.0
Config:  [0, 0, 0, 0, 1, 0]
Dist:  0.0
Random:  [0, 0, 1, 0, 0, 0]
Random Dist:  0.0
Max:  [0, 0, 0, 1, 0, 0]
Max Dist:  0.0
Config:  [0, 0, 1, 0, 0, 0]
Dist:  0.0
Random:  [0, 1, 0, 0, 0, 0]
Random Dist:  0.0
Max:  [0, 0, 1, 0, 0, 0]
Max Dist:  0.0
Config:  [0, 2, 0, 0, 1, 0]
Dist:  1.0
Random:  [0, 2, 0, 0, 1, 0]
Random Dist:  1.0
Max:  [2, 0, 0, 0, 1, 0]
Max Dist:  1.5
Config:  [0, 2, 0, 1, 0, 0]
Dist:  0.5
Random:  [0, 2, 0, 1, 0, 0]
Random Dist:  0.5
Max:  [2, 0, 0, 1, 0, 0]
Max Dist:  1.0
Config:  [0, 2, 0, 0, 0, 1]
Dist:  1.5
Random:  [2, 0, 0, 0, 0, 1]
Random Dist:  2.0
Max:  [2, 0, 0, 0, 0, 1]
Max Dist:  2.0
Config:  [0, 1, 0, 0, 0, 2]
Dist:  1.5
Random:  [0, 1, 2, 0, 0, 0]
Random Dist:  0.0
Max:  [0, 1, 0, 0, 0, 2]
Max Dist:  1.5


Config:  [0, 3, 2, 0, 1, 0]
Dist:  0.3333333333333333
Random:  [0, 0, 2, 3, 1, 0]
Random Dist:  0.0
Max:  [3, 0, 2, 0, 1, 0]
Max Dist:  0.6666666666666666
Config:  [0, 1, 4, 3, 2, 5]
Dist:  0.0
Random:  [0, 1, 4, 3, 2, 5]
Random Dist:  0.0
Max:  [0, 1, 4, 3, 2, 5]
Max Dist:  0.0
Config:  [4, 0, 1, 0, 2, 3]
Dist:  0.5
Random:  [0, 0, 1, 4, 2, 3]
Random Dist:  0.0
Max:  [4, 0, 1, 0, 2, 3]
Max Dist:  0.5
Config:  [4, 3, 0, 1, 0, 2]
Dist:  0.5
Random:  [0, 3, 0, 1, 4, 2]
Random Dist:  0.25
Max:  [4, 3, 0, 1, 0, 2]
Max Dist:  0.5
Config:  [4, 3, 0, 1, 5, 2]
Dist:  0.2
Random:  [4, 3, 5, 1, 0, 2]
Random Dist:  0.2
Max:  [4, 3, 0, 1, 5, 2]
Max Dist:  0.2
PREDICTION ACCURACY
Random : 0.13793103448275862   0.1724137931034483
Max : 0.41379310344827586 0.6206896551724138
Config:  [0, 0, 0, 1, 0, 0]
Dist:  0.0
Random:  [0, 0, 0, 0, 1, 0]
Random Dist:  0.0
Max:  [0, 0, 0, 0, 0, 1]
Max Dist:  0.0
Config:  [0, 0, 0, 0, 0, 1]
Dist:  0.0
Random:  [0, 0, 0, 1, 0, 0]
Random Dist:  0.0
Max:  [1, 0, 0, 0, 

Max Dist:  0.0
Config:  [4, 0, 1, 0, 2, 3]
Dist:  0.5
Random:  [0, 4, 1, 0, 2, 3]
Random Dist:  0.25
Max:  [4, 0, 1, 0, 2, 3]
Max Dist:  0.5
Config:  [4, 3, 0, 1, 0, 2]
Dist:  0.5
Random:  [4, 3, 0, 1, 0, 2]
Random Dist:  0.5
Max:  [4, 3, 0, 1, 0, 2]
Max Dist:  0.5
Config:  [4, 3, 0, 1, 5, 2]
Dist:  0.2
Random:  [4, 3, 5, 1, 0, 2]
Random Dist:  0.2
Max:  [4, 3, 0, 1, 5, 2]
Max Dist:  0.2
PREDICTION ACCURACY
Random : 0.3793103448275862   0.1724137931034483
Max : 0.4482758620689655 0.6206896551724138
Config:  [0, 0, 0, 1, 0, 0]
Dist:  0.0
Random:  [1, 0, 0, 0, 0, 0]
Random Dist:  0.0
Max:  [0, 0, 0, 0, 0, 0]
Max Dist:  0
Config:  [0, 0, 0, 0, 0, 1]
Dist:  0.0
Random:  [1, 0, 0, 0, 0, 0]
Random Dist:  0.0
Max:  [0, 0, 0, 0, 0, 0]
Max Dist:  0
Config:  [0, 0, 0, 0, 1, 0]
Dist:  0.0
Random:  [0, 0, 0, 0, 1, 0]
Random Dist:  0.0
Max:  [0, 0, 0, 0, 1, 0]
Max Dist:  0.0
Config:  [0, 0, 1, 0, 0, 0]
Dist:  0.0
Random:  [0, 0, 1, 0, 0, 0]
Random Dist:  0.0
Max:  [0, 0, 0, 1, 0, 0]
Max Dist:  0.0


PREDICTION ACCURACY
Random : 0.3103448275862069   0.1724137931034483
Max : 0.41379310344827586 0.6206896551724138
Config:  [0, 0, 0, 1, 0, 0]
Dist:  0.0
Random:  [1, 0, 0, 0, 0, 0]
Random Dist:  0.0
Max:  [1, 0, 0, 0, 0, 0]
Max Dist:  0.0
Config:  [0, 0, 0, 0, 0, 1]
Dist:  0.0
Random:  [0, 0, 1, 0, 0, 0]
Random Dist:  0.0
Max:  [0, 0, 0, 0, 0, 1]
Max Dist:  0.0
Config:  [0, 0, 0, 0, 1, 0]
Dist:  0.0
Random:  [0, 1, 0, 0, 0, 0]
Random Dist:  0.0
Max:  [0, 0, 1, 0, 0, 0]
Max Dist:  0.0
Config:  [0, 0, 1, 0, 0, 0]
Dist:  0.0
Random:  [0, 1, 0, 0, 0, 0]
Random Dist:  0.0
Max:  [1, 0, 0, 0, 0, 0]
Max Dist:  0.0
Config:  [0, 2, 0, 0, 1, 0]
Dist:  1.0
Random:  [0, 2, 0, 0, 1, 0]
Random Dist:  1.0
Max:  [2, 0, 0, 0, 1, 0]
Max Dist:  1.5
Config:  [0, 2, 0, 1, 0, 0]
Dist:  0.5
Random:  [0, 0, 0, 1, 2, 0]
Random Dist:  0.0
Max:  [2, 0, 0, 1, 0, 0]
Max Dist:  1.0
Config:  [0, 2, 0, 0, 0, 1]
Dist:  1.5
Random:  [2, 0, 0, 0, 0, 1]
Random Dist:  2.0
Max:  [2, 0, 0, 0, 0, 1]
Max Dist:  2.0
Config:  [0

Max Dist:  0.0
Config:  [4, 0, 1, 0, 2, 3]
Dist:  0.5
Random:  [4, 0, 1, 0, 2, 3]
Random Dist:  0.5
Max:  [4, 0, 1, 0, 2, 3]
Max Dist:  0.5
Config:  [4, 3, 0, 1, 0, 2]
Dist:  0.5
Random:  [4, 3, 0, 1, 0, 2]
Random Dist:  0.5
Max:  [4, 3, 0, 1, 0, 2]
Max Dist:  0.5
Config:  [4, 3, 0, 1, 5, 2]
Dist:  0.2
Random:  [4, 3, 0, 1, 5, 2]
Random Dist:  0.2
Max:  [4, 3, 5, 1, 0, 2]
Max Dist:  0.2
PREDICTION ACCURACY
Random : 0.4482758620689655   0.1724137931034483
Max : 0.4482758620689655 0.6206896551724138
Config:  [0, 0, 0, 1, 0, 0]
Dist:  0.0
Random:  [0, 0, 0, 0, 0, 1]
Random Dist:  0.0
Max:  [0, 0, 0, 0, 1, 0]
Max Dist:  0.0
Config:  [0, 0, 0, 0, 0, 1]
Dist:  0.0
Random:  [1, 0, 0, 0, 0, 0]
Random Dist:  0.0
Max:  [0, 0, 0, 0, 0, 0]
Max Dist:  0
Config:  [0, 0, 0, 0, 1, 0]
Dist:  0.0
Random:  [0, 1, 0, 0, 0, 0]
Random Dist:  0.0
Max:  [0, 0, 0, 1, 0, 0]
Max Dist:  0.0
Config:  [0, 0, 1, 0, 0, 0]
Dist:  0.0
Random:  [0, 0, 0, 0, 0, 1]
Random Dist:  0.0
Max:  [0, 0, 0, 0, 0, 0]
Max Dist:  0
C

...

Max Dist:  0.2
PREDICTION ACCURACY
Random : 0.1724137931034483   0.1724137931034483
Max : 0.3793103448275862 0.6206896551724138
Config:  [0, 0, 0, 1, 0, 0]
Dist:  0.0
Random:  [0, 0, 0, 1, 0, 0]
Random Dist:  0.0
Max:  [0, 0, 1, 0, 0, 0]
Max Dist:  0.0
Config:  [0, 0, 0, 0, 0, 1]
Dist:  0.0
Random:  [0, 0, 0, 1, 0, 0]
Random Dist:  0.0
Max:  [0, 0, 0, 0, 0, 0]
Max Dist:  0
Config:  [0, 0, 0, 0, 1, 0]
Dist:  0.0
Random:  [0, 0, 0, 0, 0, 1]
Random Dist:  0.0
Max:  [0, 0, 0, 0, 1, 0]
Max Dist:  0.0
Config:  [0, 0, 1, 0, 0, 0]
Dist:  0.0
Random:  [0, 0, 0, 1, 0, 0]
Random Dist:  0.0
Max:  [0, 0, 0, 1, 0, 0]
Max Dist:  0.0
Config:  [0, 2, 0, 0, 1, 0]
Dist:  1.0
Random:  [2, 0, 0, 0, 1, 0]
Random Dist:  1.5
Max:  [2, 0, 0, 0, 1, 0]
Max Dist:  1.5
Config:  [0, 2, 0, 1, 0, 0]
Dist:  0.5
Random:  [0, 0, 2, 1, 0, 0]
Random Dist:  0.0
Max:  [2, 0, 0, 1, 0, 0]
Max Dist:  1.0
Config:  [0, 2, 0, 0, 0, 1]
Dist:  1.5
Random:  [2, 0, 0, 0, 0, 1]
Random Dist:  2.0
Max:  [2, 0, 0, 0, 0, 1]
Max Dist:  2.0

Max:  [0, 1, 0, 2, 0, 3]
Max Dist:  0.6666666666666666
Config:  [3, 0, 2, 0, 1, 0]
Dist:  0.6666666666666666
Random:  [0, 0, 2, 0, 1, 3]
Random Dist:  0.3333333333333333
Max:  [3, 0, 2, 0, 1, 0]
Max Dist:  0.6666666666666666
Config:  [0, 2, 1, 0, 0, 3]
Dist:  0.6666666666666666
Random:  [0, 2, 1, 3, 0, 0]
Random Dist:  0.0
Max:  [0, 2, 1, 0, 0, 3]
Max Dist:  0.6666666666666666
Config:  [0, 1, 0, 3, 0, 2]
Dist:  0.6666666666666666
Random:  [0, 1, 0, 3, 0, 2]
Random Dist:  0.6666666666666666
Max:  [3, 1, 0, 0, 0, 2]
Max Dist:  0.6666666666666666
Config:  [0, 1, 0, 2, 0, 3]
Dist:  0.6666666666666666
Random:  [0, 1, 0, 2, 0, 3]
Random Dist:  0.6666666666666666
Max:  [0, 1, 0, 2, 0, 3]
Max Dist:  0.6666666666666666
Config:  [0, 3, 0, 2, 0, 1]
Dist:  0.6666666666666666
Random:  [0, 0, 0, 2, 3, 1]
Random Dist:  0.0
Max:  [3, 0, 0, 2, 0, 1]
Max Dist:  1.0
Config:  [0, 0, 1, 0, 2, 3]
Dist:  0.3333333333333333
Random:  [0, 0, 1, 3, 2, 0]
Random Dist:  0.0
Max:  [3, 0, 1, 0, 2, 0]
Max Dist:  0.66

Config:  [1, 0, 0, 2, 0, 3]
Dist:  1.0
Random:  [1, 3, 0, 2, 0, 0]
Random Dist:  0.3333333333333333
Max:  [1, 0, 0, 2, 0, 3]
Max Dist:  1.0
Config:  [0, 1, 0, 2, 0, 3]
Dist:  0.6666666666666666
Random:  [3, 1, 0, 2, 0, 0]
Random Dist:  0.3333333333333333
Max:  [0, 1, 0, 2, 0, 3]
Max Dist:  0.6666666666666666
Config:  [3, 0, 2, 0, 1, 0]
Dist:  0.6666666666666666
Random:  [0, 0, 2, 0, 1, 3]
Random Dist:  0.3333333333333333
Max:  [3, 0, 2, 0, 1, 0]
Max Dist:  0.6666666666666666
Config:  [0, 2, 1, 0, 0, 3]
Dist:  0.6666666666666666
Random:  [0, 2, 1, 0, 3, 0]
Random Dist:  0.3333333333333333
Max:  [0, 2, 1, 0, 0, 3]
Max Dist:  0.6666666666666666
Config:  [0, 1, 0, 3, 0, 2]
Dist:  0.6666666666666666
Random:  [0, 1, 0, 0, 3, 2]
Random Dist:  0.6666666666666666
Max:  [0, 1, 0, 3, 0, 2]
Max Dist:  0.6666666666666666
Config:  [0, 1, 0, 2, 0, 3]
Dist:  0.6666666666666666
Random:  [0, 1, 0, 2, 3, 0]
Random Dist:  0.3333333333333333
Max:  [0, 1, 0, 2, 0, 3]
Max Dist:  0.6666666666666666
Config:  [

Dist:  0.0
Random:  [0, 0, 0, 0, 1, 0]
Random Dist:  0.0
Max:  [0, 0, 0, 0, 0, 1]
Max Dist:  0.0
Config:  [0, 0, 1, 0, 0, 0]
Dist:  0.0
Random:  [0, 1, 0, 0, 0, 0]
Random Dist:  0.0
Max:  [0, 1, 0, 0, 0, 0]
Max Dist:  0.0
Config:  [0, 2, 0, 0, 1, 0]
Dist:  1.0
Random:  [2, 0, 0, 0, 1, 0]
Random Dist:  1.5
Max:  [2, 0, 0, 0, 1, 0]
Max Dist:  1.5
Config:  [0, 2, 0, 1, 0, 0]
Dist:  0.5
Random:  [0, 0, 0, 1, 2, 0]
Random Dist:  0.0
Max:  [2, 0, 0, 1, 0, 0]
Max Dist:  1.0
Config:  [0, 2, 0, 0, 0, 1]
Dist:  1.5
Random:  [0, 2, 0, 0, 0, 1]
Random Dist:  1.5
Max:  [2, 0, 0, 0, 0, 1]
Max Dist:  2.0
Config:  [0, 1, 0, 0, 0, 2]
Dist:  1.5
Random:  [0, 1, 0, 0, 0, 2]
Random Dist:  1.5
Max:  [0, 1, 0, 0, 0, 2]
Max Dist:  1.5
Config:  [1, 0, 0, 0, 2, 0]
Dist:  1.5
Random:  [1, 0, 2, 0, 0, 0]
Random Dist:  0.5
Max:  [1, 0, 0, 0, 0, 2]
Max Dist:  2.0
Config:  [0, 0, 0, 2, 0, 1]
Dist:  0.5
Random:  [0, 2, 0, 0, 0, 1]
Random Dist:  1.5
Max:  [2, 0, 0, 0, 0, 1]
Max Dist:  2.0
Config:  [0, 2, 0, 0, 1, 0]


Random:  [4, 3, 0, 1, 5, 2]
Random Dist:  0.2
Max:  [4, 3, 5, 1, 0, 2]
Max Dist:  0.2
PREDICTION ACCURACY
Random : 0.27586206896551724   0.1724137931034483
Max : 0.3793103448275862 0.6206896551724138
Config:  [0, 0, 0, 1, 0, 0]
Dist:  0.0
Random:  [0, 0, 0, 1, 0, 0]
Random Dist:  0.0
Max:  [0, 0, 0, 0, 0, 1]
Max Dist:  0.0
Config:  [0, 0, 0, 0, 0, 1]
Dist:  0.0
Random:  [0, 0, 1, 0, 0, 0]
Random Dist:  0.0
Max:  [0, 0, 0, 0, 0, 1]
Max Dist:  0.0
Config:  [0, 0, 0, 0, 1, 0]
Dist:  0.0
Random:  [0, 1, 0, 0, 0, 0]
Random Dist:  0.0
Max:  [0, 0, 0, 0, 0, 1]
Max Dist:  0.0
Config:  [0, 0, 1, 0, 0, 0]
Dist:  0.0
Random:  [0, 0, 0, 0, 1, 0]
Random Dist:  0.0
Max:  [0, 0, 0, 0, 1, 0]
Max Dist:  0.0
Config:  [0, 2, 0, 0, 1, 0]
Dist:  1.0
Random:  [2, 0, 0, 0, 1, 0]
Random Dist:  1.5
Max:  [2, 0, 0, 0, 1, 0]
Max Dist:  1.5
Config:  [0, 2, 0, 1, 0, 0]
Dist:  0.5
Random:  [0, 2, 0, 1, 0, 0]
Random Dist:  0.5
Max:  [2, 0, 0, 1, 0, 0]
Max Dist:  1.0
Config:  [0, 2, 0, 0, 0, 1]
Dist:  1.5
Random:  [0